# Making Capital Bikeshare system data usable

## Unzipping files

We'll add all of the files into a new folder (`/unzippedData`)

**Warning**: requires at least 5.63GB of space

In [1]:
import os
import zipfile

for file in os.listdir("./capitalBikeshareData"):
    filepath = "./capitalBikeshareData/" + file
    with zipfile.ZipFile(filepath, 'r') as zip_ref:
        zip_ref.extractall("./unzippedData")

## Analysing data before any further data preparation

Since we want to work on as much data as possible, we want to combine the data into one csv file. This however requires the csv files to be the same for the most part. The most important part is for each of the csv files to each have similar/same features. Let's check that.

In [2]:
import os
import pandas as pd

columnNamesDict = dict()
for file in os.listdir("./unzippedData"):
    filepath = "./unzippedData/" + file
    if not os.path.isfile(filepath):
        continue
    fileDataframe = pd.read_csv(filepath, low_memory=False)
    columnNames = ""
    for name in fileDataframe.columns:
        columnNames += name + ", "
    columnNames = columnNames[:-2]
    if columnNames not in columnNamesDict:
        print(filepath)
        print(columnNames + "\n")
        columnNamesDict[columnNames] = fileDataframe.columns.values.tolist()


./unzippedData/2010-capitalbikeshare-tripdata.csv
Duration, Start date, End date, Start station number, Start station, End station number, End station, Bike number, Member type

./unzippedData/202004-capitalbikeshare-tripdata.csv
ride_id, rideable_type, started_at, ended_at, start_station_name, start_station_id, end_station_name, end_station_id, start_lat, start_lng, end_lat, end_lng, member_casual



Csv files before April 2020 have columns `Duration`, `Start date`, `End date`, `Start station number`, `Start station`, `End station number`, `End station`, `Bike number`, `Member type`.

Csv files after April 2020 have columns `ride_id`, `rideable_type`, `started_at`, `ended_at`, `start_station_name`, `start_station_id`, `end_station_name`, `end_station_id`, `start_lat`, `start_lng`, `end_lat`, `end_lng`, `member_casual`.

We can see that Capital Bikeshare decided to implement coordinates into their data alongside stations. This likely comes from the fact that you can leave your bike or rent a bike in locations that don't classify under a station, which requires assigning a longitude and latitude value.

These factors make combining datasets difficult.


## Combining data into single files based on features

Since we have two different sets of column names / features for two different time ranges, we'll try to make one csv file for both sets.

**Warning**: takes a long time (~8 minutes) and requires at least 5.63 GB of space

In [3]:
import os
import pandas as pd
import warnings

warnings.simplefilter(action='ignore', category=FutureWarning)

combinedDataBeforeApril2020 = pd.DataFrame(
    {'Duration': [], 'Start date': [], 'End date': [], 'Start station number': [],
     'Start station': [], 'End station number': [], 'End station': [], 'Bike number': [],
     'Member type': []})

combinedDataAfterApril2020 = pd.DataFrame({'ride_id': [], 'rideable_type': [], 'started_at': [], 'ended_at': [],
                                           'start_station_name': [],
                                           'start_station_id': [], 'end_station_name': [], 'end_station_id': [],
                                           'start_lat': [],
                                           'start_lng': [],
                                           'end_lat': [], 'end_lng': [], 'member_casual': []})

columnNamesDict = set()
for file in os.listdir("./unzippedData"):
    filepath = "./unzippedData/" + file

    if not os.path.isfile(filepath):
        continue

    fileDataframe = pd.read_csv(filepath, low_memory=False,
                                dtype="string")  # String type is important to not convert integers into floats (becomes a problem by adding .0 to the end of an integer)

    if fileDataframe.columns[0] == 'ride_id':
        combinedDataAfterApril2020 = pd.concat([combinedDataAfterApril2020, fileDataframe], ignore_index=True)
    else:
        combinedDataBeforeApril2020 = pd.concat([combinedDataBeforeApril2020, fileDataframe], ignore_index=True)

combinedDataAfterApril2020.to_csv('./combinedDataAfterApril2020.csv')

combinedDataBeforeApril2020.to_csv('./combinedDataBeforeApril2020.csv')

## Assembling a combined csv file based on common features

Since the features after April 2020 are named better, we'll try to use their names.

**Warning**: takes a long time and requires at least 5.63 GB of space

In [4]:
# Function for assigning correct datatypes
def set_data_types_combined(df):
    df['started_at'] = pd.to_datetime(df['started_at'], format='ISO8601', yearfirst=True)
    df['ended_at'] = pd.to_datetime(df['started_at'], format='ISO8601', yearfirst=True)
    df.astype({"is_member": "bool"})


trimmedDataAfterApril2020 = pd.read_csv('./combinedDataAfterApril2020.csv', low_memory=False, index_col=0,
                                        dtype={"Start station number": "string", "End station number": "string"})
trimmedDataAfterApril2020.drop(columns=["ride_id", "rideable_type", "start_lat", "end_lat", "start_lng", "end_lng"],
                               axis=1, inplace=True)
trimmedDataAfterApril2020.columns = ["started_at", "ended_at", "start_station_name", "start_station_id",
                                     "end_station_name", "end_station_id", "is_member"]
trimmedDataAfterApril2020.loc[trimmedDataAfterApril2020['is_member'] == "member", 'is_member'] = True
trimmedDataAfterApril2020.loc[trimmedDataAfterApril2020['is_member'] == "casual", 'is_member'] = False

trimmedDataBeforeApril2020 = pd.read_csv('./combinedDataBeforeApril2020.csv', low_memory=False, index_col=0,
                                         dtype={"start_station_id": "string", "end_station_id": "string"})
trimmedDataBeforeApril2020.drop(columns=["Duration", "Bike number"], axis=1, inplace=True)
trimmedDataBeforeApril2020.columns = ["started_at", "ended_at", "start_station_id", "start_station_name",
                                      "end_station_id", "end_station_name", "is_member"]
trimmedDataBeforeApril2020.loc[trimmedDataBeforeApril2020['is_member'] == "Member", 'is_member'] = True
trimmedDataBeforeApril2020.loc[trimmedDataBeforeApril2020['is_member'] == "Casual", 'is_member'] = False

combinedData = pd.concat([trimmedDataAfterApril2020, trimmedDataBeforeApril2020], ignore_index=True)
set_data_types_combined(combinedData)
combinedData.to_csv('./combinedData.csv')

# In-depth analysis

## Analysing data in greater detail

Now that we have multiple large datasets, we can do further investigation into how good our data is.

Things that we'll check in no particular order:
- Checking if station IDs always go together with the same name
- Checking the amount of empty fields

In [1]:
# Loading in data if required, takes a long time
import cudf

combinedData = cudf.read_csv('./combinedData.csv', low_memory=False, index_col=0,
                           dtype={"start_station_id": "string", "end_station_id": "string"})
combinedDataAfterApril2020 = cudf.read_csv('./combinedDataAfterApril2020.csv')
combinedDataBeforeApril2020 = cudf.read_csv('./combinedDataBeforeApril2020.csv')

KeyboardInterrupt: 

### Checking for empty fields

In [17]:
def print_empty_statistics(df):
    print("Amount of rows e.g. bike rides:", f"{len(df):,}")
    rows_with_empty_fields = df.shape[0] - df.dropna().shape[0]
    print("Amount of rows in combined dataset with empty fields", f"{rows_with_empty_fields:,}")
    print("Percentage of data with empty fields:", "~" + str(round(rows_with_empty_fields / len(df) * 100, 3)) + "%")


print("Combined data:")
print_empty_statistics(combinedData)
print()

print("Data before April 2020:")
print_empty_statistics(combinedDataBeforeApril2020)
print()

print("Data after April 2020:")
print_empty_statistics(combinedDataAfterApril2020)
print()



Combined data:
Amount of rows e.g. bike rides: 37,554,003
Amount of rows in combined dataset with empty fields 2,581,716
Percentage of data with empty fields: ~6.875%

Data before april 2020:
Amount of rows e.g. bike rides: 20,380,277
Amount of rows in combined dataset with empty fields 14
Percentage of data with empty fields: ~0.0%

Data after april 2020:
Amount of rows e.g. bike rides: 17,173,726
Amount of rows in combined dataset with empty fields 2,581,726
Percentage of data with empty fields: ~15.033%



As we can see, about 7% of the combined dataset has empty fields with most of the empty fields originating from the data after April 2020.

In [20]:
combinedDataAfterApril2020.isna().sum()

ride_id                     0
rideable_type               0
started_at                  0
ended_at                    0
start_station_name    1763763
start_station_id      1763763
end_station_name      1880096
end_station_id        1880914
start_lat                  10
start_lng                  10
end_lat                 26620
end_lng                 26620
member_casual               0
dtype: int64

The main problem that creates the large amounts of empty fields is that Capital Bikeshare implemented a coordinate system, as we discussed in the chapter about column names. When people leave a bike or rent a bike at a location that isn't a designated station, then the appropriate field is left empty.

In [25]:
print("Empty fields in the data before April 2020")
empty_fields_before_42020 = combinedDataBeforeApril2020.isna().sum()
for column in combinedDataBeforeApril2020.columns:
    if empty_fields_before_42020[column] != 0:
        print(column + ":", empty_fields_before_42020[column])

Empty fields in the data before April 2020
Bike number: 14


Seems like the only source of empty fields in the data before April 2020 is the bike numbers. This however is such a tiny sum, that we can easily remove the related rows without worry.

### Checking if all station IDs align with their names

In [35]:
name_to_id_dictionary = dict()

def add_id_name_to_dict_and_check_for_discrepancy(df, name_column, id_column, dictionary):
    for index, row in df.iterrows():
        station_name = row[name_column]
        station_id = row[id_column]
        if station_name is None or station_id is None:
            continue
        if station_name in dictionary:
            dictionary[station_name].append(station_id)
        else:
            dictionary[station_name] = {station_id}



Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with name nan has two IDs: nan and nan
Station with 

KeyboardInterrupt: 